In [21]:
## Import necessary packages

%matplotlib osx 
# On Macs use osx
# For Windows use qt

import numpy as np
from numpy.random import rand
#from landscapeWithOcean import LandscapeWithOcean # Import methods from inside file landscapeWithOcean.py

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm

from matplotlib.animation import FFMpegWriter
metadata = dict(title="hw09.mp4", artist='Matplotlib',comment='They are not actually chocolate.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
#fig = plt.figure(dpi=200)

In [22]:
nx=np.outer(np.linspace(0,75,num=75), np.ones(75))
ny=nx.copy().T


wave1=np.ones((75,75))*30
for wave in range(7):
    if wave<5:
        wave1[wave][0:50]+=wave
    else:
        wave1[wave][0:50]+=(7-wave)

wave2=np.ones((75,75))*30
for depth in range(75):
    if depth>=67 and depth<=71:
        wave2[depth]+=np.abs(67-depth)
    if depth>71:
        wave2[depth]+=np.abs(74-depth)
        
        
land = np.ones((75,75))
for depth in range(75):
    land[depth]=25
    for coast in range(75):
        if depth<coast and coast<=25:
            land[depth][coast]=depth+np.abs(25-coast)
        if depth+coast<=50 and depth<25 and coast>25:
            land[depth][coast]=depth+np.abs(25-coast)
        
        
fig = plt.figure(figsize =(14, 9)) 
ax = plt.axes(projection ='3d') 

ax.plot_surface(nx, ny, wave1, color='xkcd:sky blue')
ax.plot_surface(nx,ny, wave2, color='xkcd:sky blue')
ax.plot_surface(nx,ny,land, color='xkcd:light tan')

plt.show()

In [27]:
fig=plt.figure()
new_ocean=np.copy(wave1)
with writer.saving(fig, "animation.mp4", dpi=100):
    peak_depth=4
    w2_peak=71
    for it in range(71):
        peak=np.max(new_ocean[peak_depth])
        for depth in range(1,75):
            if depth+4>=w2_peak:
                wave2[depth]+=1
            if depth>w2_peak+3:
                wave2[depth]-=1
            if depth<peak_depth:
                #return to 30
                #ocean[depth]=peak*(peak_depth-depth)**2
                new_depth = np.abs(peak - (peak_depth-depth))
                if new_depth>30:
                    new_ocean[depth]=new_depth  * 0.78
                else:
                    new_ocean[depth]=30
            #new_ocean[depth]=np.abs(peak - (peak_depth-depth))
            if depth>peak_depth:
                #return to 30
                if depth<=peak_depth+(peak-30):
                    #new_ocean[depth] = peak * (1 / (peak_depth - depth))
                    #new_ocean[depth] = new_ocean[peak_depth] * (1 - (0.1 / (depth - peak_depth)))
                    new_ocean[depth] = (peak_depth / depth)*(peak-30)  * 0.78
                else:
                    new_ocean[depth] = 30
            else:
                slope=land[depth]-land[depth-1]
                if any(slope):
                    new_ocean[depth]=new_ocean[depth-1]+slope  #Water is displaced so it is forced upwards
                else:
                    new_ocean[depth]=new_ocean[depth-1]*0.98  #Force of gravity pushes water back down
                    for p in range(75):
                        if new_ocean[depth][p]<30:
                            new_ocean[depth][p]=30
        peak_depth+=1
        w2_peak-=1

    #fig = plt.figure(figsize =(14, 9)) 
        if it%3==0:
            fig.clear()
            ax = plt.axes(projection ='3d') 

            ax.plot_surface(nx, ny, new_ocean+wave2, color='xkcd:ocean blue')
            #ax.plot_surface(nx,ny, wave2, color='xkcd:sky blue')
            ax.plot_surface(nx,ny,land, color='xkcd:light tan')

            plt.show()
            plt.pause(0.01)
            writer.grab_frame()